In [32]:
import itertools
import pandas as pd
import numpy as np
import toytree
import toyplot
import arviz as az
import pymc3 as pm
from pymc3.distributions.dist_math import normal_lccdf, normal_lcdf

### Load tree

In [2]:
EXCLUDE = [
    'Quercus|Quercus|Leucomexicana|Q.species', 
    'Quercus|Quercus|Roburoids|Q.vulcanica',
    'Quercus|Quercus|Roburoids|Q.imeretina', 
    'Quercus|Lobatae|Erythromexicana|Q.lowilliamsii', 
    'Quercus|Lobatae|Agrifoliae|Q.oxyadenia',
    'Quercus|Quercus|Dumosae|Q.pacifica',
    'Quercus|Quercus|Roburoids|Q.kotschyana',
    'Quercus|Quercus|Roburoids|Q.cedrorum', 
    'Quercus|Lobatae|Agrifoliae|Q.tamalpaiensis',
    'Cerris|Cyclobalanopsis|Semiserrata|Q.litoralis', 
    'Cerris|Cyclobalanopsis|Semiserrata|Q.patelliformis',
    'Cerris|Cyclobalanopsis|Glauca|Q.multinervis', 
    'Cerris|Ilex|Himalayansubalpine|Q.sp.nov.',
]

TREE = toytree.tree("/home/henry/oaks-thesis/full_crown2.tre").drop_tips(EXCLUDE)

# find duplicates (label ends in 1 or 2, we'll drop the 2)
DUPS = [i for i in TREE.get_tip_labels() if i.endswith('2')]
TREE = TREE.drop_tips(DUPS)

# relabel kept duplicate tips by stripping 1 from end
TREE = TREE.set_node_values(
    feature="name", 
    values={nidx: TREE.idx_dict[nidx].name.strip("1") for nidx in TREE.idx_dict}
)

# Scale tree to 1.0 length
TREE = TREE.mod.node_scale_root_height(1.0)

In [3]:
# Get crown nodes for eight clades.
clades = [
    "Quercus|Quercus", # teal
    "Quercus|Virentes", # orange
    "Quercus|Ponticae", # blue
    "Quercus|Protobalanus", # pink
    "Quercus|Lobatae", # green
    "Cerris|Ilex", # yellow
    "Cerris|Cerris", # tan
    "Cerris|Cyclobalanopsis", # gray
]
crowns = {
    TREE.get_mrca_idx_from_tip_labels(wildcard=i): i for i in clades
}
crowns

{419: 'Quercus|Quercus',
 420: 'Quercus|Virentes',
 434: 'Quercus|Ponticae',
 447: 'Quercus|Protobalanus',
 455: 'Quercus|Lobatae',
 450: 'Cerris|Ilex',
 451: 'Cerris|Cerris',
 457: 'Cerris|Cyclobalanopsis'}

In [78]:
# draw the tree
TREE.draw(
    layout='d', 
    edge_colors=TREE.get_edge_values_mapped({
            j: toytree.colors[i] for i,j in enumerate(crowns)
        }),
    tip_labels=False,
    height=350,
    node_labels=[
        str(i) if int(i) in crowns else "" 
        for i in TREE.get_node_values("idx", 1, 1)
    ],
    node_labels_style={
        "font-size": "16px",
        "-toyplot-anchor-shift": "15px",
    },
);

<svg class="toyplot-canvas-Canvas" height="350.0px" id="t252e19a1d63e44abb687dc21b5a29cee" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 1000.0 350.0" width="1000.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> 419 420 434 447 450 451 455 457

In [5]:
# make group index (gidx)
crown_dict = {i: TREE.get_tip_labels(i) for i in crowns}
gidx = np.zeros(TREE.ntips, dtype=int)
for tidx, tip in enumerate(TREE.get_tip_labels()):
    for cidx, clade in enumerate(crown_dict):
        if tip in crown_dict[clade]:
            gidx[tidx] = cidx
gidx

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1,
       1, 1, 1, 2, 2, 3, 3, 3, 3, 3, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
       4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
       4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
       4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 5, 5, 5, 5, 5, 5, 5, 5,
       5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6,
       6, 6, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7,
       7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7])

In [92]:
# True param values
𝛼_mean = 0.05
𝛼_std = 0.02
𝛽_mean = 1.5
𝛽_std = 0.2
𝜓_mean = 0.0
𝜓_std = 0.33
𝜎_std = 0.05

# 8 different clade effects on rate of RI (used for partial-pooling data)
𝜓_Quercus_mean = -0.8
𝜓_Quercus_std = 0.2
𝜓_Virentes_mean = -3.5
𝜓_Virentes_std = 0.05
𝜓_Ponticae_mean = -5.0
𝜓_Ponticae_std = 0.05
𝜓_Protobalanus_mean = 5.0
𝜓_Protobalanus_std = 0.1
𝜓_Lobatae_mean = 0.5
𝜓_Lobatae_std = 0.2
𝜓_Ilex_mean = 1.0
𝜓_Ilex_std = 0.15
𝜓_Cerris_mean = 5.0
𝜓_Cerris_std = 0.15
𝜓_Cyclobalanopsis_mean = 3.5
𝜓_Cyclobalanopsis_std = 0.15

In [93]:
SPECIES_DATA = pd.DataFrame({
    "Species": ["Quercus " + "{}".format(
        TREE.idx_dict[idx].name.split("|")[-1].split(".")[-1]) for idx in range(len(TREE.get_tip_labels()))],
    "b": np.random.normal(𝛽_mean, 𝛽_std, TREE.ntips),
    "psi": np.random.normal(𝜓_mean, 𝜓_std, TREE.ntips),
    "psi_x": np.concatenate([
        np.random.normal(𝜓_Quercus_mean, 𝜓_Quercus_std, len(gidx[gidx == 0])),
        np.random.normal(𝜓_Virentes_mean, 𝜓_Virentes_std, len(gidx[gidx == 1])),
        np.random.normal(𝜓_Ponticae_mean, 𝜓_Ponticae_std, len(gidx[gidx == 2])),
        np.random.normal(𝜓_Protobalanus_mean, 𝜓_Protobalanus_std, len(gidx[gidx == 3])),
        np.random.normal(𝜓_Lobatae_mean, 𝜓_Lobatae_std, len(gidx[gidx == 4])),
        np.random.normal(𝜓_Ilex_mean, 𝜓_Ilex_std, len(gidx[gidx == 5])),
        np.random.normal(𝜓_Cerris_mean, 𝜓_Cerris_std, len(gidx[gidx == 6])),
        np.random.normal(𝜓_Cyclobalanopsis_mean, 𝜓_Cyclobalanopsis_std, len(gidx[gidx == 7])),
    ]),
    "gidx": gidx
})

In [94]:
SPECIES_DATA

Species         b       psi     psi_x  gidx
0       Quercus arizonica  1.039668 -0.539341 -0.725920     0
1    Quercus oblongifolia  0.935657  0.343521 -0.782573     0
2           Quercus laeta  1.192648 -0.053157 -0.790907     0
3        Quercus ajoensis  1.236735  0.578182 -0.983472     0
4      Quercus turbinella  1.339171 -0.166233 -0.431400     0
..                    ...       ...       ...       ...   ...
226           Quercus rex  1.701366 -0.512669  3.245336     7
227       Quercus chungii  1.332709  0.272657  3.463437     7
228      Quercus delavayi  1.243064  0.121348  3.387540     7
229    Quercus championii  1.771993 -0.386972  3.363444     7
230         Quercus gilva  1.426521 -0.319770  3.507336     7

[231 rows x 5 columns]

### Generate crossing data

In [95]:
def get_dist(tree, idx0, idx1):
    "returns the genetic distance between two nodes on a tree"
    dist = tree.treenode.get_distance(
        tree.idx_dict[idx0], 
        tree.idx_dict[idx1],
    )
    return dist

In [96]:
# get all combinations of two sampled taxa
a, b = zip(*itertools.combinations(range(TREE.ntips), 2))

# organize into DF and get genetic distance between pairs
DATA = pd.DataFrame({
    "sidx0": a,
    "sidx1": b,
    "dist": [(get_dist(TREE, i, j) / 2) for (i, j) in zip(a, b)],
})

DATA['b'] = np.random.normal(𝛽_mean, 𝛽_std, DATA.shape[0])
DATA['velo'] = (
    DATA['b']
    + SPECIES_DATA['psi'][DATA.sidx0].values
    + SPECIES_DATA['psi'][DATA.sidx1].values
)
DATA['velo_x'] = (
    DATA['b']
    + SPECIES_DATA['psi_x'][DATA.sidx0].values
    + SPECIES_DATA['psi_x'][DATA.sidx1].values
)
DATA['intercept'] = np.random.normal(𝛼_mean, 𝛼_std, DATA.shape[0])
DATA['error'] = np.random.normal(0.0, 𝜎_std, DATA.shape[0])

DATA['RI_pooled'] = DATA.intercept + (DATA.b * DATA.dist) + DATA.error
DATA['RI_unpooled'] = DATA.intercept + (DATA.velo * DATA.dist) + DATA.error
DATA['RI_partpooled'] = DATA.intercept + (DATA.velo_x * DATA.dist) + DATA.error

In [97]:
# censor values in range 0-1
DATA.loc[DATA['RI_pooled'] < 0, 'RI_pooled'] = 0
DATA.loc[DATA['RI_pooled'] > 1, 'RI_pooled'] = 1
DATA.loc[DATA['RI_unpooled'] < 0, 'RI_unpooled'] = 0
DATA.loc[DATA['RI_unpooled'] > 1, 'RI_unpooled'] = 1
DATA.loc[DATA['RI_partpooled'] < 0, 'RI_partpooled'] = 0
DATA.loc[DATA['RI_partpooled'] > 1, 'RI_partpooled'] = 1

In [98]:
NSAMPLES = 1000
SAMPLE = DATA.sample(NSAMPLES).copy().reset_index(drop=True)
SAMPLE.head()

sidx0  sidx1      dist         b      velo    velo_x  intercept     error  \
0    117    124  0.202624  1.561005  1.332040  2.943831   0.045231 -0.019468   
1     99    137  0.303937  1.162081  1.015756  1.833451   0.066827 -0.113267   
2     89    126  0.927411  1.295275  0.634826 -1.598571   0.089949 -0.004743   
3    109    153  0.455905  1.721255  1.798275  2.888131   0.057384  0.049880   
4     84    101  0.927411  1.517356  1.843818 -1.564768   0.038786  0.066345   

   RI_pooled  RI_unpooled  RI_partpooled  
0   0.342060     0.295667       0.622255  
1   0.306759     0.262285       0.510812  
2   1.000000     0.673951       0.000000  
3   0.891992     0.927105       1.000000  
4   1.000000     1.000000       0.000000

### Visualize data

In [99]:
canvas = toyplot.Canvas(width=350, height=300)
axes = canvas.cartesian(
    label="Pooled data",
    xlabel="Genetic dist.",
    ylabel="Reprod. incomp.",
)

# points are jittered on x-axis for visibility
axes.scatterplot(
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    size=8,
    opacity=0.25,
    color=SAMPLE.loc[:, 'RI_pooled'].values,
    mstyle={"stroke": "black"},
);
axes.x.ticks.show = True
axes.y.ticks.show = True

<svg class="toyplot-canvas-Canvas" height="300.0px" id="t0ffc07f6c4a54194acae5ed73d8c5523" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 350.0 300.0" width="350.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" style="fill:rgb(40.4%,0%,12.2%);fill-opacity:1.0;opacity:0.25;stroke:rgb(0%,0%,0%);stroke-opac

In [100]:
canvas = toyplot.Canvas(width=350, height=300)
axes = canvas.cartesian(
    label="Unpooled data",
    xlabel="Genetic dist.",
    ylabel="Reprod. incomp.",
)

# points are jittered on x-axis for visibility
axes.scatterplot(
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    size=8,
    opacity=0.25,
    color=SAMPLE.loc[:, 'RI_unpooled'].values,
    mstyle={"stroke": "black"},
);
axes.x.ticks.show = True
axes.y.ticks.show = True

<svg class="toyplot-canvas-Canvas" height="300.0px" id="t8bd52dcc1c7c4c94a00dc3ba0db3cd58" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 350.0 300.0" width="350.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" style="fill:rgb(40.4%,0%,12.2%);fill-opacity:1.0;opacity:0.25;

In [101]:
canvas = toyplot.Canvas(width=350, height=300)
axes = canvas.cartesian(
    label="Partpooled data",
    xlabel="Genetic dist.",
    ylabel="Reprod. incomp.",
)

# points are jittered on x-axis for visibility
axes.scatterplot(
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    size=8,
    opacity=0.25,
    color=SAMPLE.loc[:, 'RI_partpooled'].values,
    mstyle={"stroke": "black"},
);
axes.x.ticks.show = True
axes.y.ticks.show = True

<svg class="toyplot-canvas-Canvas" height="300.0px" id="t8441dac8a73b443e9eb899974f3df6cb" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 350.0 300.0" width="350.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" style="fill:rgb(40.4

### Functions to plot results

In [102]:
def toytrace(trace, var_names, titles):
    """
    Plot posterior trace with toyplot
    """
    nvars = len(var_names)
    
    # setup canvase
    canvas = toyplot.Canvas(width=500, height=200 * nvars)
    
    # store axes
    axes = []
    
    # iter over params
    for pidx, param in enumerate(var_names):
        
        # get param posterior
        posterior = trace.get_values(param)
        
        # setup axes 
        ax = canvas.cartesian(grid=(nvars, 1, pidx))
        ax.y.show = False
        ax.x.spine.style = {"stroke-width": 1.5}
        ax.x.ticks.labels.style = {"font-size": "12px"}
        ax.x.ticks.show = True
        ax.x.label.text = f"param='{titles[pidx]}'"        
        
        # iterate over shape of param
        for idx in range(posterior.shape[1]):
            mags, bins = np.histogram(posterior[:, idx], bins=100)
            ax.plot(bins[1:], mags, stroke_width=2, opacity=0.6)
        axes.append(ax)
    return canvas, axes

In [20]:
import scipy.stats as stats

def draw_velocity_dists(trace, baseline=0.15):
    """
    Draw the clade velocities as gaussians
    """
    canvas = toyplot.Canvas(width=350, height=300)
    axes = canvas.cartesian(xlabel="Relative velocity of reproductive isolation")
    marks = []
    base = 0
    for i in range(trace['𝜓_mean'].shape[1]):
        
        loc = trace['𝜓_mean'][:, i].mean()
        scale = trace['𝜓_std'][:, i].mean()
        interval = stats.norm.interval(0.995, loc, scale)
        points = np.linspace(interval[0], interval[1], 100)
        mark = axes.fill(
            points, 
            stats.norm.pdf(points, loc=loc, scale=scale), 
            style={
                "fill-opacity": 0.45,
                "stroke": 'black',
                "stroke-opacity": 1.0,
                "stroke-width": 1,
            },
            baseline=np.repeat(base, 100),
        )
        marks.append(mark)
        axes.hlines(base, style={"stroke-dasharray": "5,5", 'stroke-width': 1})
        base += baseline
        
    axes.y.show = False
    axes.x.ticks.locator = toyplot.locator.Extended(only_inside=True)
    axes.x.ticks.show = True
    return canvas, axes, marks

In [21]:
def rmse(predictions, targets):
    differences = predictions - targets                       #the DIFFERENCEs.
    differences_squared = differences ** 2                    #the SQUAREs of ^
    mean_of_differences_squared = differences_squared.mean()  #the MEAN of ^
    rmse_val = np.sqrt(mean_of_differences_squared)           #ROOT of ^
    return rmse_val                                           #get the ^

### Define models

In [22]:
def censored_pooled_regression(x, y, **kwargs):
    
    # data pre-processing
    lower_censored = y[y <= 0].index
    _x_lc = x[lower_censored].values
    _y_lc = y[lower_censored].values

    upper_censored = y[y >= 1].index
    _x_uc = x[upper_censored].values
    _y_uc = y[upper_censored].values

    uncensored = (y > 0) & (y < 1)
    _x = x[uncensored].values
    _y = y[uncensored].values
    
    # define model
    with pm.Model() as model:  

        # parameters and error
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        𝜎 = pm.HalfNormal('𝜎', 5.0, shape=1)

        # linear model prediction
        ri = 𝛼 + 𝛽 * _x

        # data likelihood (normal distributed errors)
        y = pm.Normal("y", mu=ri, sigma=𝜎, observed=_y)

        # density of censored data
        if sum(lower_censored):
            lcensored = pm.Potential(
                "lower_censored", 
                normal_lcdf(𝛼 + 𝛽 * _x_lc, 𝜎, _y_lc),
            )
        if sum(upper_censored):
            ucensored = pm.Potential(
                "upper_censored",
                normal_lccdf(𝛼 + 𝛽 * _x_uc, 𝜎, _y_uc),
            )

        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]
    
        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [23]:
def censored_unpooled_noncentered_regression(x, y, idx0, idx1, **kwargs):
    
    # data pre-processing
    lower_censored = y[y <= 0].index
    _x_lc = x[lower_censored].values
    _y_lc = y[lower_censored].values

    upper_censored = y[y >= 1].index
    _x_uc = x[upper_censored].values
    _y_uc = y[upper_censored].values

    uncensored = (y > 0) & (y < 1)
    _x = x[uncensored].values
    _y = y[uncensored].values
    
    # define model
    with pm.Model() as model:
        
        # censored indexers
        sidx0 = pm.Data("spp_idx0", idx0.values[uncensored])
        sidx1 = pm.Data("spp_idx1", idx1.values[uncensored])
        sidx0_u = pm.Data("sidx0_u", idx0.values[upper_censored])
        sidx1_u = pm.Data("sidx1_u", idx1.values[upper_censored])
        sidx0_l = pm.Data("sidx0_l", idx0.values[lower_censored])
        sidx1_l = pm.Data("sidx1_l", idx1.values[lower_censored])

        # parameters and error
        𝜓_mean = pm.Normal('𝜓_mean', mu=0., sigma=5., shape=1)
        𝜓_std = pm.HalfNormal('𝜓_std', 5., shape=1)
        𝜓_offset = pm.Normal('𝜓_offset', mu=0, sigma=1., shape=TREE.ntips)
        𝜓 = pm.Deterministic('𝜓', 𝜓_mean + 𝜓_std * 𝜓_offset)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝜎 = pm.HalfNormal('𝜎', 5., shape=1)
        
        # linear model prediction
        ri = 𝛼 + (𝛽 + 𝜓[sidx0] + 𝜓[sidx1]) * _x

        # data likelihood (normal distributed errors)
        y = pm.Normal("y", mu=ri, sigma=𝜎, observed=_y)

        # density of censored data
        if sum(lower_censored):
            lcensored = pm.Potential(
                "lower_censored", 
                normal_lcdf(𝛼 + (𝛽 + 𝜓[sidx0_l] + 𝜓[sidx1_l]) * _x_lc, 𝜎, _y_lc),
            )
        
        if sum(upper_censored):
            ucensored = pm.Potential(
                "upper_censored",
                normal_lccdf(𝛼 + (𝛽 + 𝜓[sidx0_u] + 𝜓[sidx1_u]) * _x_uc, 𝜎, _y_uc),
            )

        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]

        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [24]:
def censored_partpooled_noncentered_regression(x, y, idx0, idx1, gidx, **kwargs):
    
    # data pre-processing
    lower_censored = y[y <= 0].index
    _x_lc = x[lower_censored].values
    _y_lc = y[lower_censored].values

    upper_censored = y[y >= 1].index
    _x_uc = x[upper_censored].values
    _y_uc = y[upper_censored].values

    uncensored = (y > 0) & (y < 1)
    _x = x[uncensored].values
    _y = y[uncensored].values
    
    # define model
    with pm.Model() as model:
        
        # censored indexers
        sidx0 = pm.Data("spp_idx0", idx0.values[uncensored])
        sidx1 = pm.Data("spp_idx1", idx1.values[uncensored])
        sidx0_u = pm.Data("sidx0_u", idx0.values[upper_censored])
        sidx1_u = pm.Data("sidx1_u", idx1.values[upper_censored])
        sidx0_l = pm.Data("sidx0_l", idx0.values[lower_censored])
        sidx1_l = pm.Data("sidx1_l", idx1.values[lower_censored])
        gidx = pm.Data("gidx", gidx)

        # parameters and error
        𝜓_mean = pm.Normal('𝜓_mean', mu=0., sigma=5., shape=8)
        𝜓_std = pm.HalfNormal('𝜓_std', 5., shape=8)
        𝜓_offset = pm.Normal('𝜓_offset', mu=0, sigma=1., shape=TREE.ntips)
        𝜓 = pm.Deterministic('𝜓', 𝜓_mean[gidx] + 𝜓_std[gidx] * 𝜓_offset)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝜎 = pm.HalfNormal('𝜎', 5., shape=1)
        
        # linear model prediction
        ri = 𝛼 + (𝛽 + 𝜓[sidx0] + 𝜓[sidx1]) * _x

        # data likelihood (normal distributed errors)
        y = pm.Normal("y", mu=ri, sigma=𝜎, observed=_y)

        # density of censored data
        if sum(lower_censored):
            lcensored = pm.Potential(
                "lower_censored", 
                normal_lcdf(𝛼 + (𝛽 + 𝜓[sidx0_l] + 𝜓[sidx1_l]) * _x_lc, 𝜎, _y_lc),
            )
        
        if sum(upper_censored):
            ucensored = pm.Potential(
                "upper_censored",
                normal_lccdf(𝛼 + (𝛽 + 𝜓[sidx0_u] + 𝜓[sidx1_u]) * _x_uc, 𝜎, _y_uc),
            )

        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]

        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

### Run models

In [103]:
# MCMC sampler kwargs
sample_kwargs = dict(
    tune=4000,
    draws=4000,
    target_accept=0.95,
    return_inferencedata=False,
    progressbar=True,
)

In [104]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_sub = censored_pooled_regression(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝜎, 𝛽, 𝛼]


Sampling 4 chains for 4_000 tune and 4_000 draw iterations (16_000 + 16_000 draws total) took 69 seconds.


In [105]:
pooled_sub['stats']

mean     sd  hdi_3%  hdi_97%  mcse_mean  mcse_sd  ess_mean  ess_sd  \
𝛼[0]  0.107  0.016   0.076    0.136        0.0      0.0    4165.0  4138.0   
𝛽[0]  1.279  0.032   1.220    1.338        0.0      0.0    4047.0  4047.0   
𝜎[0]  0.121  0.006   0.110    0.134        0.0      0.0    4994.0  4984.0   

      ess_bulk  ess_tail  r_hat  
𝛼[0]    4172.0    5172.0    1.0  
𝛽[0]    4044.0    4642.0    1.0  
𝜎[0]    5011.0    5752.0    1.0

In [109]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
unpooled_sub = censored_unpooled_noncentered_regression(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝜎, 𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 4_000 tune and 4_000 draw iterations (16_000 + 16_000 draws total) took 7698 seconds.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The estimated number of effective samples is smaller than 200 for some parameters.


In [36]:
toytrace(unpooled_sub['trace'], ['𝜓_mean', '𝜓_offset', '𝜓'], ['psi-mean', 'psi-offset', 'psi-spp']);

<svg class="toyplot-canvas-Canvas" height="600.0px" id="t2ea1f743ceb3472390c0c9cecd8538d0" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 600.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <path d="M 50.0 149.43977591036418 L 54.040404040404056 149.43977591036418 L 58.08080808080808 150.0 L 62.12121212121214 148.8795518207283 L 66.16161616161617 149.1596638655462 L 70.20202020202021 149.1596638655462 L 74.24242424242426 148.0392156862745 L 78.28282828282829 147.75910364145656 L 82.32323232323235 148.0392156862745 L 86.36363636363637 147.19887955182074 L 90.4040404040404 146.07843137254903 L 94.44444444444446 142.43697478991598 L 98.4848484848485 146.35854341736695 L 102.52525252525254 145.51820728291315 L 106.56565656565658 142.7170868347339 L 110.60606060606062 141.03641456582633 L 114.64646464646466 141.8767507002801 L 118.6868686868687 138.79551820728292 L 122.72727272727273 136.55462184873952 L 126.76767676767678 135.99439775910363 L 130.80808080808083 137.67507002801122 L 134.84848484848487 127.03081232492998 L 138.8888888888889 127.59103641456583 L 142.92929292929296 123.38935574229693 L 146.969696969697 123.109243697479 L 151.010101010101 120.02801120448179 L 155.05050505050505 119.74789915966386 L 159.09090909090912 110.50420168067228 L 163.13131313131316 114.14565826330531 L 167.17171717171718 102.38095238095238 L 171.21212121212122 103.78151260504201 L 175.25252525252523 98.4593837535014 L 179.2929292929293 95.09803921568627 L 183.33333333333337 89.2156862745098 L 187.37373737373736 91.17647058823529 L 191.41414141414145 94.81792717086833 L 195.45454545454547 77.73109243697479 L 199.4949494949495 86.69467787114846 L 203.53535353535355 72.40896358543418 L 207.57575757575756 71.28851540616247 L 211.61616161616163 65.96638655462185 L 215.6565656565657 59.523809523809526 L 219.6969696969697 57.84313725490197 L 223.73737373737376 55.88235294117647 L 227.77777777777777 52.52100840336134 L 231.81818181818184 58.123249299719895 L 235.85858585858588 53.921568627450974 L 239.89898989898992 57.84313725490197 L 243.93939393939397 57.2829131652661 L 247.979797979798 50.0 L 252.02020202020202 51.120448179271705 L 256.06060606060606 55.602240896358545 L 260.1010101010101 55.602240896358545 L 264.14141414141415 57.84313725490197 L 268.1818181818182 64.00560224089635 L 272.22222222222223 65.12605042016807 L 276.26262626262627 78.8515406162465 L 280.3030303030303 83.0532212885154 L 284.34343434343435 84.45378151260505 L 288.3838383838384 80.53221288515405 L 292.42424242424244 85.85434173669466 L 296.4646464646464 96.21848739495799 L 300.5050505050505 102.10084033613444 L 304.54545454545456 101.26050420168066 L 308.5858585858586 108.8235294117647 L 312.6262626262626 112.18487394957982 L 316.66666666666674 106.02240896358543 L 320.7070707070707 111.90476190476191 L 324.7474747474747 118.34733893557423 L 328.7878787878788 120.58823529411764 L 332.82828282828285 128.99159663865547 L 336.8686868686869 129.55182072829132 L 340.90909090909093 131.51260504201682 L 344.949494949495 131.23249299719888 L 348.989898989899 137.11484593837534 L 353.030303030303 137.39495798319328 L 357.0707070707071 140.7563025210084 L 361.1111111111111 143.27731092436974 L 365.1515151515152 143.55742296918768 L 369.1919191919192 146.07843137254903 L 373.2323232323232 144.11764705882354 L 377.27272727272725 145.79831932773112 L 381.3131313131314 146.63865546218486 L 385.3535353535354 148.0392156862745 L 389.3939393939394 148.31932773109244 L 393.4343434343434 148.0392156862745 L 397.4747474747475 146.63865546218486 L 401.51515151515156 148.59943977591038 L 405.55555555555554 149.43977591036418 L 409.5959595959596 

In [37]:
# show plot of TRUE vs. ESTIMATED rates
c, a, m = toyplot.scatterplot(
    unpooled_sub['trace']['𝜓'].mean(axis=0),         # estimated
    SPECIES_DATA['psi'],                             # true
    width=400,
    height=250,
    xlabel="ESTIMATED species velocity",
    ylabel="TRUE species velocity",
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t221929c5fd3d457186aa32bcb7c9b1a4" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 400.0 250.0" width="400.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> -0.5 0.0 0.5 1.0 ESTIMATED species velocity -1.0 -0.5 0.0 0.5 1.0 TRUE species velocity

In [106]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_sub = censored_partpooled_noncentered_regression(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝜎, 𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 4_000 tune and 4_000 draw iterations (16_000 + 16_000 draws total) took 8274 seconds.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The number of effective samples is smaller than 10% for some parameters.


In [107]:
toytrace(partpooled_sub['trace'], ['𝜓_mean', '𝜓_offset', '𝜓'], ['psi-mean', 'psi-offset', 'psi-spp']);

<svg class="toyplot-canvas-Canvas" height="600.0px" id="tbfb5673ed72648bfaac561feb2751f04" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 600.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <path d="M 148.6698204515884 149.7991967871486 L 149.89725939957714 150.0 L 151.1246983475658 149.7991967871486 L 152.3521372955545 150.0 L 153.57957624354322 150.0 L 154.80701519153192 149.7991967871486 L 156.03445413952062 150.0 L 157.2618930875093 149.59839357429718 L 158.489332035498 150.0 L 159.71677098348673 149.7991967871486 L 160.9442099314754 149.7991967871486 L 162.1716488794641 149.59839357429718 L 163.3990878274528 149.19678714859438 L 164.6265267754415 148.99598393574297 L 165.85396572343024 148.59437751004018 L 167.0814046714189 148.79518072289156 L 168.30884361940758 148.39357429718876 L 169.53628256739634 147.18875502008032 L 170.76372151538501 146.18473895582326 L 171.99116046337372 147.79116465863453 L 173.21859941136242 147.99196787148594 L 174.44603835935112 146.3855421686747 L 175.6734773073398 144.97991967871488 L 176.90091625532853 142.570281124498 L 178.12835520331723 141.36546184738955 L 179.35579415130593 143.97590361445785 L 180.5832330992946 143.7751004016064 L 181.8106720472833 140.36144578313252 L 183.038110995272 141.16465863453814 L 184.26554994326074 134.13654618473896 L 185.4929888912494 135.140562248996 L 186.72042783923814 129.51807228915663 L 187.94786678722681 128.9156626506024 L 189.17530573521555 126.90763052208837 L 190.40274468320422 123.49397590361447 L 191.63018363119292 123.09236947791163 L 192.85762257918162 115.66265060240963 L 194.0850615271703 111.24497991967873 L 195.31250047515897 107.63052208835342 L 196.53993942314773 106.02409638554218 L 197.76737837113643 105.82329317269077 L 198.9948173191251 101.60642570281125 L 200.2222562671138 101.20481927710841 L 201.44969521510248 100.0 L 202.67713416309124 96.78714859437753 L 203.9045731110799 89.5582329317269 L 205.1320120590686 86.74698795180723 L 206.35945100705734 76.70682730923696 L 207.58688995504602 69.87951807228916 L 208.81432890303472 89.5582329317269 L 210.0417678510234 79.71887550200805 L 211.26920679901212 77.71084337349399 L 212.4966457470008 70.48192771084337 L 213.72408469498953 75.90361445783132 L 214.9515236429782 73.89558232931726 L 216.1789625909669 77.91164658634538 L 217.40640153895563 74.8995983935743 L 218.6338404869443 80.52208835341366 L 219.861279434933 81.92771084337349 L 221.08871838292168 84.73895582329317 L 222.31615733091039 86.54618473895582 L 223.54359627889914 88.95582329317268 L 224.77103522688782 94.97991967871485 L 225.99847417487652 94.37751004016064 L 227.22591312286522 103.4136546184739 L 228.4533520708539 106.82730923694778 L 229.68079101884263 106.42570281124499 L 230.90822996683133 108.63453815261043 L 232.13566891482 113.05220883534137 L 233.36310786280873 118.67469879518073 L 234.5905468107974 116.06425702811245 L 235.81798575878614 121.48594377510041 L 237.04542470677478 126.50602409638553 L 238.2728636547635 127.9116465863454 L 239.5003026027522 129.51807228915663 L 240.72774155074092 137.14859437751002 L 241.95518049872965 135.3413654618474 L 243.18261944671832 139.75903614457832 L 244.41005839470702 139.5582329317269 L 245.6374973426957 139.15662650602408 L 246.86493629068443 139.75903614457832 L 248.09237523867313 141.16465863453814 L 249.3198141866618 145.38152610441767 L 250.54725313465053 142.77108433734938 L 251.77469208263923 144.97991967871488 L 253.0021310306279 144.57831325301206 L 254.22956997861667 147.99196787148594 L 255.4570089266053 146.9879518072289 L 256.68444787459407 147.59036144578315 L 257.9118868225827 148.39357429718876 L 2

In [108]:
# show plot of TRUE vs. ESTIMATED rates
c, a, m = toyplot.scatterplot(
    partpooled_sub['trace']['𝜓'].mean(axis=0),         # estimated
    SPECIES_DATA['psi_x'],                             # true
    width=400,
    height=250,
    xlabel="ESTIMATED species velocity",
    ylabel="TRUE species velocity",
    color=[toytree.colors[i] for i in SPECIES_DATA.gidx],
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t91b5438f43154d71b5885fd18a679979" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 400.0 250.0" width="400.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> -10 -5 0 5 10 ESTIMATED species velocity -5 0 5 TRUE species velocity